<a href="https://colab.research.google.com/github/sc0les/nba_prediction_markets/blob/main/WIP_Data_Transformation_%26_Feature_Generation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
from functools import reduce
import warnings
warnings.filterwarnings('ignore')
pd.set_option('display.max_columns', 1500)
from google.colab import drive
drive.mount('/content/drive/')

# Data Transformations

Although one can argue that transformations is still part of the data cleansing process, I segmented the notebooks since the following data transformations help explain the final data schema we'll achieve for model ingestion.

We excluded the joining of the Player Game data from the rest of the merged datasets due to difference in table schemas. As seen below, each player's game performance is stored in a separate line item. 

Since we'll be sizing down this dataset, it made sense to do this prior to joining it with the rest of the tables we've procured thus far.

In [ ]:
player_stats_df = pd.read_csv('/content/drive/My Drive/Sam Colelli BSTN Capstone/Datasets/game_stats.csv', index_col = 0)
player_stats_df

GAME_ID       TEAM_ID TEAM_ABBREVIATION    TEAM_CITY  PLAYER_ID  \
0   20700459  1.610613e+09               NJN   New Jersey     2210.0   
1   20700459  1.610613e+09               NJN   New Jersey   201157.0   
2   20700459  1.610613e+09               NJN   New Jersey   200767.0   
3   20700459  1.610613e+09               NJN   New Jersey     1713.0   
4   20700459  1.610613e+09               NJN   New Jersey      467.0   
..       ...           ...               ...          ...        ...   
20  21900139  1.610613e+09               LAL  Los Angeles  1627936.0   
21  21900139  1.610613e+09               LAL  Los Angeles   203584.0   
22  21900139  1.610613e+09               LAL  Los Angeles   201162.0   
23  21900139  1.610613e+09               LAL  Los Angeles     2730.0   
24  21900139  1.610613e+09               LAL  Los Angeles  1629659.0   

            PLAYER_NAME NICKNAME START_POSITION                 COMMENT  \
0     Richard Jefferson  Richard              F                     NaN   
1         Sean Williams     Sean              F                     NaN   
2            Josh Boone     Josh              C                     NaN   
3          Vince Carter    Vince              G                     NaN   
4            Jason Kidd    Jason              G                     NaN   
..                  ...      ...            ...                     ...   
20          Alex Caruso     Alex            NaN                     NaN   
21         Troy Daniels     Troy            NaN                     NaN   
22         Jared Dudley    Jared            NaN                     NaN   
23        Dwight Howard   Dwight            NaN                     NaN   
24  Talen Horton-Tucker    Talen            NaN  DNP - Coach's Decision   

      MIN  E_OFF_RATING  OFF_RATING  E_DEF_RATING  DEF_RATING  E_NET_RATING  \
0   38:37         103.5       108.1         107.4       109.3          -4.0   
1   16:00          94.5        96.6         123.7       122.6         -29.2   
2   16:07         103.9       106.9         115.6       113.3         -11.8   
3   41:36          99.5       103.8          99.9       103.8          -0.4   
4   37:05         107.6       112.7         104.7       107.0           2.9   
..    ...           ...         ...           ...         ...           ...   
20  17:22         124.0       118.4         129.1       136.1          -5.0   
21  17:19         110.9       105.3         116.0       116.7          -5.2   
22   2:02          77.3        75.0         100.0        80.0         -22.7   
23  16:51         109.4       108.6         114.3       123.5          -4.8   
24    NaN           NaN         0.0           NaN         0.0           NaN   

    NET_RATING  AST_PCT  AST_TOV  AST_RATIO  OREB_PCT  DREB_PCT  REB_PCT  \
0         -1.2    0.083     0.67        9.5     0.000     0.054    0.027   
1        -26.0    0.200     0.00       33.3     0.063     0.417    0.214   
2         -6.4    0.000     0.00        0.0     0.050     0.273    0.129   
3          0.0    0.250     6.00       22.2     0.093     0.068    0.080   
4          5.6    0.308     2.67       38.1     0.000     0.278    0.135   
..         ...      ...      ...        ...       ...       ...      ...   
20       -17.7    0.267     4.00       44.4     0.000     0.111    0.059   
21       -11.4    0.000     0.00        0.0     0.000     0.200    0.111   
22        -5.0    0.000     0.00        0.0     0.000     0.000    0.000   
23       -15.0    0.000     0.00        0.0     0.105     0.200    0.154   
24         0.0      NaN      NaN        NaN     0.000     0.000    0.000   

    TM_TOV_PCT  EFG_PCT  TS_PCT  USG_PCT  E_USG_PCT  E_PACE    PACE  \
0         14.3    0.333   0.416    0.224      0.223   95.49   92.60   
1          0.0    0.250   0.225    0.125      0.123   90.54   90.00   
2          0.0    0.250   0.410    0.143      0.144   88.22   87.86   
3          3.7    0.382   0.458    0.236      0.235   94.36   90.58   
4         14.3    0.37

By the end of this data transformation process, all single game-specific data will live within a single row to align with our target variable. This means that each player's game stats will need to transposed into columns in the table.

To achieve this, while also attempting to keep the dataset to a manageable size, `START_POSITION` will be the key variable leveraged for this transformation.

The ultimate downfall of this decision is that bench player performance will be ignored. Many domain experts will argue that strong bench players can be key to a team's success. However, due to the `NaN` that is tied to each bench player, it would be difficult to craft an expanable signal.

There are potential future remediations, such as feature engineering to subtract starting player performance from overall team performance, or to fetch addtional datasets that can provide positional information for each bench player.

In [ ]:
#removing bench players
start_players = player_stats_df[player_stats_df['START_POSITION'].notna()]

#dropping unneeded, categorical columns
start_players.drop(columns = ['TEAM_ABBREVIATION', 'TEAM_CITY', 'NICKNAME', 'COMMENT'], inplace = True)

#creating tmp_id for later join with merged dataset
start_players['TEAM_ID'] = start_players['TEAM_ID'].astype('int')
start_players['tmp_id'] = start_players['TEAM_ID'].astype('str') + start_players['GAME_ID'].astype('str')

In [ ]:
# fetching the full dataset, dropping repeated columns
stats_spread_df = pd.read_csv('/content/drive/My Drive/Sam Colelli BSTN Capstone/Datasets/full_game_stats.csv', index_col = 0)
final_stats_spread = stats_spread_df

In [ ]:
#separating home and away teams for easier join with player game stats (now there is only 1 team per GAME_ID)
home_away_df = final_stats_spread[['TEAM_ID', 'GAME_ID', 'home_away']]
home_away_df.loc[:,'tmp_id'] = home_away_df.loc[:,'TEAM_ID'].astype('str') + home_away_df.loc[:,'GAME_ID'].astype('str')
home_away_df = home_away_df[['tmp_id', 'home_away']]

In [ ]:
#merging home team stats with player stats for that game
start_players_vh = pd.merge(home_away_df, start_players, on = 'tmp_id')
start_players_vh.drop_duplicates(inplace = True)

In the NBA, there are 5 starting positions:
* Point Guard (PG)
* Shooting Guard (SG)
* Small Forward (SF)
* Power Forward (PF)
* Center (C)

While there is a clear difference in terms of skillset and abilities within each position, they can be generally grouped into 3 positions, as they are in the Player Game dataset:
* Guard (both PG & SG)
* Forward (both SF & PF)
* Center (C)

However, it is not advised to aggregate the stats across these positions, as specific players can have major roles in team success, even when their counter parts in an adjacent position to not perform as well.

The current solution to this is to associate each position with an enumeration, providing a segmentation between the general position designations specified in that dataset.

In [ ]:
mask = start_players_vh[['START_POSITION']].duplicated(keep = False)
start_players_vh.loc[mask, 'START_POSITION'] += start_players_vh.groupby(['GAME_ID', 'TEAM_ID', 'START_POSITION']).cumcount().add(1).astype(str)

In [ ]:
start_players_vh

tmp_id home_away   GAME_ID     TEAM_ID  PLAYER_ID  \
0       161061275120700459         V  20700459  1610612751     2210.0   
1       161061275120700459         V  20700459  1610612751   201157.0   
2       161061275120700459         V  20700459  1610612751   200767.0   
3       161061275120700459         V  20700459  1610612751     1713.0   
4       161061275120700459         V  20700459  1610612751      467.0   
...                    ...       ...       ...         ...        ...   
237040  161061274721900139         H  21900139  1610612747     2544.0   
237041  161061274721900139         H  21900139  1610612747   203076.0   
237042  161061274721900139         H  21900139  1610612747   201580.0   
237043  161061274721900139         H  21900139  1610612747   201980.0   
237044  161061274721900139         H  21900139  1610612747   202340.0   

              PLAYER_NAME START_POSITION    MIN  E_OFF_RATING  OFF_RATING  \
0       Richard Jefferson             F1  38:37         103.5       108.1   
1           Sean Williams             F2  16:00          94.5        96.6   
2              Josh Boone             C1  16:07         103.9       106.9   
3            Vince Carter             G1  41:36          99.5       103.8   
4              Jason Kidd             G2  37:05         107.6       112.7   
...                   ...            ...    ...           ...         ...   
237040       LeBron James             F1  35:20         105.4       102.7   
237041      Anthony Davis             F2  37:40          95.4        96.3   
237042       JaVale McGee             C1  14:21          97.1       100.0   
237043        Danny Green             G1  27:14         102.7       103.4   
237044      Avery Bradley             G2  31:23          97.1        95.6   

        E_DEF_RATING  DEF_RATING  E_NET_RATING  NET_RATING  AST_PCT  AST_TOV  \
0              107.4       109.3          -4.0        -1.2    0.083     0.67   
1              123.7       122.6         -29.2       -26.0    0.200     0.00   
2              115.6       113.3         -11.8        -6.4    0.000     0.00   
3               99.9       103.8          -0.4         0.0    0.250     6.00   
4              104.7       107.0           2.9         5.6    0.308     2.67   
...              ...         ...           ...         ...      ...      ...   
237040         106.4       112.2          -0.9        -9.5    0.625     7.50   
237041          97.1       103.8          -1.7        -7.5    0.143     0.60   
237042          90.8        86.7           6.3        13.3    0.000     0.00   
237043         103.2       108.6          -0.5        -5.2    0.083     2.00   
237044          86.8        90.9          10.3         4.7    0.174     4.00   

        AST_RATIO  OREB_PCT  DREB_PCT  REB_PCT  TM_TOV_PCT  EFG_PCT  TS_PCT  \
0             9.5     0.000     0.054    0.027        14.3    0.333   0.416   
1            33.3     0.063     0.417    0.214         0.0    0.250   0.225   
2             0.0     0.050     0.273    0.129         0.0    0.250   0.410   
3            22.2     0.093     0.068    0.080         3.7    0.382   0.458   
4            38.1     0.000     0.278    0.135        14.3    0.375   0.512   
...           ...       ...       ...      ...         ...      ...     ...   
237040       42.9     0.067     0.278    0.160         5.7    0.333   0.368   
237041        9.7     0.067     0.122    0.093        16.1    0.550   0.596   
237042        0.0     0.059     0.250    0.138         8.3    0.455   0.455   
237043       25.0     0.029     0.080    0.051        12.5    0.000   0.000   
237044       26.7     0.079     0.030    0.056         6.7    0.450   0.450   

        USG_PCT  E_USG_PCT  E_PACE    PACE  PACE_PER40  POSS    PIE  
0         0.224      0.223   95.49   92.60       77.17  74.0  0.034  
1         0.125      0.123   90.54   90.00       75.00  29.0 -0.010  
2         0.143      0.144   88.22   87.86       73.22  29.0  0.010  
3         0.236      0.235  

In [ ]:
#converting playing time to seconds to incorporate into player stat augmentation shortly after
start_players_vh[['MIN', 'SEC']] = start_players_vh['MIN'].str.split(':', expand = True)
start_players_vh['MIN'] = start_players_vh['MIN'].astype('int') * 60
start_players_vh['PLAYING_TIME_S'] = start_players_vh['MIN'].astype('int') + start_players_vh['SEC'].astype('int')
start_players_vh.drop(columns = ['MIN', 'SEC'], inplace = True)

Now that we have such segmentation, we can transform that line-by-line player data into columns for the same game.

#### Note: The following renamed columns was an assumption based on domain knowledge and eye-test of the Player Game data. For the most part, most Point Guards were the last `G` and most Small Forwards were the first `F` specified for each game, and therefore their position designations are reflected this way in the below script.

In [ ]:
f1 = start_players_vh[(start_players_vh['START_POSITION'] == 'F1')]
f2 = start_players_vh[(start_players_vh['START_POSITION'] == 'F2')]
g1 = start_players_vh[(start_players_vh['START_POSITION'] == 'G1')]
g2 = start_players_vh[(start_players_vh['START_POSITION'] == 'G2')]
c = start_players_vh[(start_players_vh['START_POSITION'] == 'C1')]

df_list = [g2, g1, f1, f2, c]
df_name_list = ['PG', 'SG', 'SF', 'PF', 'C']

for i, df in enumerate(df_list, 0):
    df.drop(columns = ['GAME_ID', 'TEAM_ID', 'home_away', 'START_POSITION'], inplace = True)
    df.columns = [f'{df_name_list[i]}_'.format(i) + col_name for col_name in df.columns]
    df = df.rename(columns = {f'{df_name_list[i]}_tmp_id': 'tmp_id'}, inplace = True)
    
id_df = start_players_vh[['tmp_id', 'GAME_ID', 'TEAM_ID']]

test_df = reduce(lambda left, right: pd.merge(left, right, on = ['tmp_id'], how = 'outer'), df_list)
test_df = pd.merge(test_df, id_df, on = ['tmp_id'], how = 'inner')
test_df.drop_duplicates(inplace = True)
test_df

tmp_id  PG_PLAYER_ID PG_PLAYER_NAME  PG_E_OFF_RATING  \
0       161061275120700459         467.0     Jason Kidd            107.6   
5       161061275320700459        2306.0  Carlos Arroyo            125.9   
10      161061275120700476         467.0     Jason Kidd             98.4   
15      161061276620700476         976.0   Jeff McInnis             96.5   
20      161061275120700484         467.0     Jason Kidd            110.1   
...                    ...           ...            ...              ...   
191375  161061274721700076     1628366.0     Lonzo Ball             82.0   
191380  161061276121800139      200768.0     Kyle Lowry            137.3   
191385  161061274721800139     1628366.0     Lonzo Ball            115.1   
191390  161061276121900139     1627832.0  Fred VanVleet             92.8   
191395  161061274721900139      202340.0  Avery Bradley             97.1   

        PG_OFF_RATING  PG_E_DEF_RATING  PG_DEF_RATING  PG_E_NET_RATING  \
0               112.7            104.7          107.0              2.9   
5               128.1            106.6          110.7             19.3   
10              101.1            100.1          103.5             -1.7   
15               98.8            101.2          102.4             -4.7   
20              111.8             93.9           93.5             16.2   
...               ...              ...            ...              ...   
191375           80.0             97.0          101.5            -15.0   
191380          137.5            101.2          105.8             36.1   
191385          120.4            121.7          117.6             -6.6   
191390           96.3            104.0          102.4            -11.2   
191395           95.6             86.8           90.9             10.3   

        PG_NET_RATING  PG_AST_PCT  PG_AST_TOV  PG_AST_RATIO  PG_OREB_PCT  \
0                 5.6       0.308        2.67          38.1        0.000   
5                17.4       0.333        0.00          36.8        0.040   
10               -2.4       0.414        4.00          46.2        0.021   
15               -3.7       0.200        5.00          35.7        0.000   
20               18.3       0.452        2.00          41.2        0.095   
...               ...         ...         ...           ...          ...   
191375          -21.5       0.300        1.50          35.3        0.034   
191380           31.7       0.455       15.00          42.9        0.031   
191385            2.8       0.235        2.00          30.8        0.050   
191390           -6.1       0.455        3.33          30.3        0.000   
191395            4.7       0.174        4.00          26.7        0.079   

        PG_DREB_PCT  PG_REB_PCT  PG_TM_TOV_PCT  PG_EFG_PCT  PG_TS_PCT  \
0             0.278       0.135           14.3       0.375      0.512   
5             0.077       0.059            0.0       0.556      0.687   
10            0.250       0.119           11.5       0.450      0.506   
15            0.049       0.028            7.1       0.813      0.813   
20            0.209       0.153           20.6       0.318      0.392   
...             ...         ...            ...         ...        ...   
191375        0.182       0.113           23.5       0.357      0.357   
191380        0.161       0.095            2.9       0.500      0.528   
191385        0.348       0.209           15.4       0.857      0.857   
191390        0.156       0.082            9.1       0.556      0.582   
191395        0.030       0.056            6.7       0.450      0.450   

        PG_USG_PCT  PG_E_USG_PCT  PG_E_PACE  PG_PACE  PG_PACE_PER40  PG_POSS  \
0            0.159         0.158      95.06    91.90          76.58     71.0   
5            0.188         0.190      92.72    90.20          75.17     57.0   
10           0.139         0.141     106.53   103.31          86.09     87.0   
15           0.105         0.104     104.45   102.59          85.49     81.0   
20           0.190         0

In [ ]:
#ID table for future merge
id_df = final_stats_spread[['GAME_ID', 'SEASON_ID', 'GAME_DATE_y']]

In [ ]:
#merging ID table with player stats
full_player = pd.merge(test_df, id_df, on = 'GAME_ID', how = 'inner')
full_player.drop_duplicates(inplace = True)
full_player.to_csv('/Users/scolelli/Downloads/normalized_player_stats.csv')

# Preliminary Feature Generation

Now that the Player Game stats are properly stored, the next step is to create features based on these stats. It is important to remember that all of these stats are lagging indicators and cannot be used for model training. Instead, they need to be augmented to (1) remove any bias of data that cannot be seen in production but (2) still captures how player performance can influence team performance and game outcomes.

To do so, a script was created find the moving average of game stats (not including current game) for the previous 1 game, 3 games, 5 games, and 7 games. In addition, the cumulative average over the season was also calculated.

In [ ]:
#changing dtypes prior to MA script
full_player['GAME_DATE_y'] = pd.to_datetime(full_player['GAME_DATE_y'])
full_player['PG_PLAYER_ID'] = full_player['PG_PLAYER_ID'].astype(str)
full_player['SG_PLAYER_ID'] = full_player['SG_PLAYER_ID'].astype(str)
full_player['SF_PLAYER_ID'] = full_player['SF_PLAYER_ID'].astype(str)
full_player['PF_PLAYER_ID'] = full_player['PF_PLAYER_ID'].astype(str)
full_player['C_PLAYER_ID'] = full_player['C_PLAYER_ID'].astype(str)
full_player.sort_values('GAME_DATE_y', inplace = True)

In [ ]:
season_cummean = pd.DataFrame({})
prev_game = pd.DataFrame({})
three_game_ma = pd.DataFrame({})
five_game_ma = pd.DataFrame({})
seven_game_ma = pd.DataFrame({})

df_list = [prev_game, three_game_ma, five_game_ma, seven_game_ma]
x = 1

for df in df_list:
    for col in full_player.select_dtypes(['int', 'float']):
        df[f'{x}DAY_MA_{col}'] = full_player.groupby(['SEASON_ID', 'TEAM_ID'])[col].transform(lambda y: y.rolling(x, min_periods = x).mean().shift())
    df['tmp_id'] = full_player['GAME_ID'].astype(str) + full_player['TEAM_ID'].astype(str)
    df = df.drop(columns = [f'{x}DAY_MA_GAME_ID', f'{x}DAY_MA_TEAM_ID', f'{x}DAY_MA_SEASON_ID'], inplace = True)
    x += 2

pos_list = ['PG', 'SG', 'SF', 'PF', 'C']

for col in full_player.select_dtypes(['int', 'float']):
    season_cummean[f'SEASON_MA_{col}'] = full_player.groupby(['SEASON_ID', 'TEAM_ID'])[col].apply(lambda y: y.shift().expanding().mean())
    for pos in pos_list:
        season_cummean[f'{pos}_PLAYER_ID'] = full_player[f'{pos}_PLAYER_ID']
season_cummean['GAME_ID'] = full_player['GAME_ID'].astype(str)
season_cummean['TEAM_ID'] = full_player['TEAM_ID'].astype(str)
season_cummean['tmp_id'] = season_cummean['GAME_ID'] + season_cummean['TEAM_ID']
season_cummean.drop(columns = [f'SEASON_MA_GAME_ID', f'SEASON_MA_TEAM_ID', f'SEASON_MA_SEASON_ID'], inplace = True) 

full_df_list = [season_cummean, prev_game, three_game_ma, five_game_ma, seven_game_ma]

ma_player = reduce(lambda left, right: pd.merge(left, right, on = ['tmp_id'], how = 'outer'), full_df_list)

In [ ]:
#removing any NAs from rolling MA/Cumulative mean
ma_player.fillna(0, inplace = True)
ma_player

SEASON_MA_PG_E_OFF_RATING PG_PLAYER_ID SG_PLAYER_ID SF_PLAYER_ID  \
0                       0.000000       2225.0        714.0       1477.0   
1                       0.000000        965.0        977.0       2575.0   
2                       0.000000       1747.0       1503.0       2203.0   
3                       0.000000     101127.0     200750.0     101110.0   
4                       0.000000     101114.0     200758.0       1905.0   
...                          ...          ...          ...          ...   
38275                 113.127778     201939.0     202691.0     203952.0   
38276                 109.238095     203935.0    1627759.0    1628369.0   
38277                 113.163158     201939.0     202691.0     203952.0   
38278                 108.650000     203935.0    1627759.0    1628369.0   
38279                 113.330000     201939.0     202691.0     203952.0   

      PF_PLAYER_ID C_PLAYER_ID  SEASON_MA_PG_OFF_RATING  \
0           1495.0    101177.0                 0.000000   
1         101142.0      2198.0                 0.000000   
2         101236.0      2397.0                 0.000000   
3         200746.0      2038.0                 0.000000   
4           2430.0      2246.0                 0.000000   
...            ...         ...                      ...   
38275     203490.0    203110.0               114.733333   
38276     201143.0   1629057.0               111.033333   
38277     203490.0    203110.0               114.800000   
38278     201143.0   1629057.0               110.418182   
38279     203490.0    203110.0               114.995000   

       SEASON_MA_PG_E_DEF_RATING  SEASON_MA_PG_DEF_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                 112.505556               114.550000   
38276                 104.057143               105.409524   
38277                 111.852632               113.847368   
38278                 104.363636               105.686364   
38279                 111.185000               113.090000   

       SEASON_MA_PG_E_NET_RATING  SEASON_MA_PG_NET_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                   0.611111                 0.194444   
38276                   5.190476                 5.614286   
38277                   1.300000                 0.963158   
38278                   4.295455                 4.722727   
38279                   2.135000                 1.915000   

       SEASON_MA_PG_AST_PCT  SEASON_MA_PG_AST_TOV  SEASON_MA_PG_AST_RATIO  \
0                  0.000000              0.000000                0.000000   
1                  0.000000              0.000000                0.000000   
2                  0.000000              0.000000                0.000000   
3                  0.000000              0.000000                0.000000   
4                  0.000000              0.000000                0.000000   
...                     ...                   ...                     ...   
38275              0.265000              2.571111               20.522222   
38276              0.253714              2.960476               26.233333   
38277              0.261053              2.477895               19.984211   
38278              0.246955              2.848636               25.436364   
38279              0.261350              2.754000               20.235000   

      

Performing the same calculation, but this time for overall team stats, not individual players.

In [ ]:
final_stats_spread.to_csv('game_stats_preprocessed.csv')

In [ ]:
team_stats = final_stats_spread.drop(columns = ['year', 'Month', 'Day', 'id', 'Final', 'ML', 'spread_open', 'spread_close', 'spread_2H', 'total_open', 'total_close', 'total_2H'])
team_stats.sort_values('GAME_DATE_y', inplace = True)

In [ ]:
season_cummean = pd.DataFrame({})
prev_game = pd.DataFrame({})
three_game_ma = pd.DataFrame({})
five_game_ma = pd.DataFrame({})
seven_game_ma = pd.DataFrame({})

df_list = [prev_game, three_game_ma, five_game_ma, seven_game_ma]
x = 1

for df in df_list:
    for col in team_stats.select_dtypes(['int', 'float']):
        df[f'team_{x}DAY_MA_{col}'] = team_stats.groupby(['SEASON_ID', 'TEAM_ID'])[col].transform(lambda y: y.rolling(x, min_periods = x).mean().shift())
    df['tmp_id'] = team_stats['GAME_ID'].astype(str) + team_stats['TEAM_ID'].astype(str)
    df = df.drop(columns = [f'team_{x}DAY_MA_GAME_ID', f'team_{x}DAY_MA_TEAM_ID', f'team_{x}DAY_MA_SEASON_ID'], inplace = True)
    x += 2

for col in team_stats.select_dtypes(['int', 'float']):
    season_cummean[f'team_SEASON_MA_{col}'] = team_stats.groupby(['SEASON_ID', 'TEAM_ID'])[col].apply(lambda y: y.shift().expanding().mean())

season_cummean['GAME_ID'] = team_stats['GAME_ID'].astype(str)
season_cummean['TEAM_ID'] = team_stats['TEAM_ID'].astype(str)
season_cummean['tmp_id'] = season_cummean['GAME_ID'] + season_cummean['TEAM_ID']
season_cummean.drop(columns = [f'team_SEASON_MA_GAME_ID', f'team_SEASON_MA_TEAM_ID', f'team_SEASON_MA_SEASON_ID'], inplace = True) 

full_df_list = [season_cummean, prev_game, three_game_ma, five_game_ma, seven_game_ma]

ma_team = reduce(lambda left, right: pd.merge(left, right, on = ['tmp_id'], how = 'outer'), full_df_list)

In [ ]:
#removing any NAs from rolling MA/Cumulative mean
ma_team.fillna(0, inplace = True)
ma_team

team_SEASON_MA_1st  team_SEASON_MA_2nd  team_SEASON_MA_3rd  \
0                0.000000            0.000000            0.000000   
1                0.000000            0.000000            0.000000   
2                0.000000            0.000000            0.000000   
3                0.000000            0.000000            0.000000   
4                0.000000            0.000000            0.000000   
...                   ...                 ...                 ...   
38275           26.277778           26.666667           30.777778   
38276           26.190476           28.190476           26.047619   
38277           26.315789           26.421053           30.736842   
38278           25.727273           27.954545           26.454545   
38279           26.350000           26.300000           30.400000   

       team_SEASON_MA_4th  team_SEASON_MA_MIN  team_SEASON_MA_PTS  \
0                0.000000            0.000000            0.000000   
1                0.000000            0.000000            0.000000   
2                0.000000            0.000000            0.000000   
3                0.000000            0.000000            0.000000   
4                0.000000            0.000000            0.000000   
...                   ...                 ...                 ...   
38275           29.611111          240.055556          113.333333   
38276           27.238095          240.142857          107.666667   
38277           29.526316          240.105263          113.000000   
38278           26.909091          240.045455          107.045455   
38279           29.500000          240.100000          112.550000   

       team_SEASON_MA_FGM  team_SEASON_MA_FGA  team_SEASON_MA_FG_PCT  \
0                0.000000            0.000000               0.000000   
1                0.000000            0.000000               0.000000   
2                0.000000            0.000000               0.000000   
3                0.000000            0.000000               0.000000   
4                0.000000            0.000000               0.000000   
...                   ...                 ...                    ...   
38275           41.777778           85.444444               0.491389   
38276           37.428571           82.238095               0.455714   
38277           41.684211           85.736842               0.488684   
38278           37.136364           81.909091               0.453773   
38279           41.650000           85.850000               0.487550   

       team_SEASON_MA_FG3M  team_SEASON_MA_FG3A  team_SEASON_MA_FG3_PCT  \
0                 0.000000             0.000000                0.000000   
1                 0.000000             0.000000                0.000000   
2                 0.000000             0.000000                0.000000   
3                 0.000000             0.000000                0.000000   
4                 0.000000             0.000000                0.000000   
...                    ...                  ...                     ...   
38275            13.888889            36.388889                0.383222   
38276            13.857143            37.238095                0.367286   
38277            13.947368            36.736842                0.381421   
38278            13.727273            37.000000                0.366227   
38279            13.700000            36.900000                0.373600   

       team_SEASON_MA_FTM  team_SEASON_MA_FTA  team_SEASON_MA_FT_PCT  \
0                0.000000            0.000000               0.000000   
1                0.000000            0.000000               0.000000   
2                0.000000            0.000000               0.000000   
3                0.000000            0.000000               0.000000   
4                0.000000            0.000000               0.000000   
...                   ...                 ...                    ...   
38275           15.888889           20.944444               0.762667   
38276  

In [ ]:
# merging team stats with player stats (finally)
ma_df = pd.merge(ma_player, ma_team, on = ['tmp_id'], how = 'outer')

Probably the one of the most important indicators of current team strength and future performance is Win/Loss Record and Percentage. Surprisingly, this was not as straight forward as I imagined it would be. Although we do already have the a `WL` column indicating if a team won or lost, creating a cumulative sum for each required some work.

The biggest issue was `.cumsum()` does not offset like `.cumcount()` does. In addition, for both `.cumcount()` and `.cumsum()`, backfilling and frontfilling the Wins and Losses was somewhat difficult to the fact they are mutually exclusive.

Instead, I first calculated `GAMES_PLAYED`, since it was an easy cumulative count. I then did the same for `WIN_TOTAL` and performed a frontfill and backfill where necessary. Then, to calculate `LOSS_TOTAL`, I simply subtracted `WIN_TOTAL` from `GAMES_PLAYED`. I also included `WIN_PCT`, as its a commonly used stat among enthusiats, and as we'll see in the modeling stages, it is also one of the, if not the strongest feature relative to Win/Loss game outcome.

In [ ]:
game_results = final_stats_spread[['WL', 'TEAM_ID', 'GAME_ID', 'SEASON_ID', 'GAME_DATE_y', 'home_away', 'Final']]
game_results.sort_values('GAME_DATE_y', inplace = True)
game_results['GAMES_PLAYED'] = game_results.groupby(['TEAM_ID', 'SEASON_ID'])['WL'].cumcount()
game_results['WIN_TOTAL'] = game_results[game_results['WL'] == 'W'].groupby(['TEAM_ID', 'SEASON_ID'])['WL'].cumcount()
game_results['WIN_TOTAL'] = game_results.groupby(['TEAM_ID', 'SEASON_ID'], sort = False)['WIN_TOTAL'].apply(lambda x: x.ffill().bfill())
game_results['LOSS_TOTAL'] = game_results['GAMES_PLAYED'] - game_results['WIN_TOTAL']
game_results['WIN_PCT'] = game_results['WIN_TOTAL'] / game_results['GAMES_PLAYED']
game_results.fillna(0, inplace = True)

In [ ]:
#temp ID for merging with full dataset
game_results['tmp_id'] = game_results['GAME_ID'].astype(str) + game_results['TEAM_ID'].astype(str)

#mapping WL column for target variable creation (will be clear in notebook shortly)
game_results['WL'] = game_results['WL'].map({'W': 1, 'L':0})

gtp_df = pd.merge(game_results, ma_df, on = ['tmp_id'], how = 'outer')
gtp_df

WL     TEAM_ID   GAME_ID  SEASON_ID GAME_DATE_y home_away  Final  \
0       1  1610612759  20700001      22007  2007-10-30         H    106   
1       0  1610612747  20700002      22007  2007-10-30         H     93   
2       1  1610612745  20700002      22007  2007-10-30         V     95   
3       0  1610612757  20700001      22007  2007-10-30         V     97   
4       1  1610612762  20700003      22007  2007-10-30         V    117   
...    ..         ...       ...        ...         ...       ...    ...   
38275   1  1610612744  42100404      42021  2022-06-10         V    107   
38276   0  1610612738  42100405      42021  2022-06-13         V     94   
38277   1  1610612744  42100405      42021  2022-06-13         H    104   
38278   0  1610612738  42100406      42021  2022-06-16         H     90   
38279   1  1610612744  42100406      42021  2022-06-16         V    103   

       GAMES_PLAYED  WIN_TOTAL  LOSS_TOTAL   WIN_PCT              tmp_id  \
0                 0        0.0         0.0  0.000000  207000011610612759   
1                 0        0.0         0.0  0.000000  207000021610612747   
2                 0        0.0         0.0  0.000000  207000021610612745   
3                 0        0.0         0.0  0.000000  207000011610612757   
4                 0        0.0         0.0  0.000000  207000031610612762   
...             ...        ...         ...       ...                 ...   
38275            18       12.0         6.0  0.666667  421004041610612744   
38276            21       13.0         8.0  0.619048  421004051610612738   
38277            19       13.0         6.0  0.684211  421004051610612744   
38278            22       13.0         9.0  0.590909  421004061610612738   
38279            20       14.0         6.0  0.700000  421004061610612744   

       SEASON_MA_PG_E_OFF_RATING PG_PLAYER_ID SG_PLAYER_ID SF_PLAYER_ID  \
0                       0.000000       2225.0        714.0       1477.0   
1                       0.000000        965.0        977.0       2575.0   
2                       0.000000       1747.0       1503.0       2203.0   
3                       0.000000     101127.0     200750.0     101110.0   
4                       0.000000     101114.0     200758.0       1905.0   
...                          ...          ...          ...          ...   
38275                 113.127778     201939.0     202691.0     203952.0   
38276                 109.238095     203935.0    1627759.0    1628369.0   
38277                 113.163158     201939.0     202691.0     203952.0   
38278                 108.650000     203935.0    1627759.0    1628369.0   
38279                 113.330000     201939.0     202691.0     203952.0   

      PF_PLAYER_ID C_PLAYER_ID  SEASON_MA_PG_OFF_RATING  \
0           1495.0    101177.0                 0.000000   
1         101142.0      2198.0                 0.000000   
2         101236.0      2397.0                 0.000000   
3         200746.0      2038.0                 0.000000   
4           2430.0      2246.0                 0.000000   
...            ...         ...                      ...   
38275     203490.0    203110.0               114.733333   
38276     201143.0   1629057.0               111.033333   
38277     203490.0    203110.0               114.800000   
38278     201143.0   1629057.0               110.418182   
38279     203490.0    203110.0               114.995000   

       SEASON_MA_PG_E_DEF_RATING  SEASON_MA_PG_DEF_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                 112.505556               114.550000   
38276                 104.057143               105.409524   
38277                 111.852632  

The last player and team stat augmentation to do (*for now*) is to provide a ranking. This ranking represents how that team or player's cumulative statistical performance ranks among their cohort at that point in time. This will provide the model more context as to how this stat should be perceived relative to other players/teams.

In [ ]:
#fetching all team and player stats
full_stats_df = gtp_df.drop(columns = ['WL', 'TEAM_ID', 'GAME_ID', 'GAME_DATE_y', 'home_away', 'Final', 'WIN_TOTAL', 'LOSS_TOTAL', 'PG_PLAYER_ID', 'SG_PLAYER_ID', 'SF_PLAYER_ID', 'PF_PLAYER_ID', 'C_PLAYER_ID'])
full_stats_df['tmp_id'] = full_stats_df['tmp_id'].astype(object)

In [ ]:
for col in full_stats_df.select_dtypes(exclude = ['object']):
    full_stats_df[f'{col}_rank'] = full_stats_df.groupby(['SEASON_ID', 'GAMES_PLAYED'])[col].rank('max')

full_stats_df.drop(columns = ['SEASON_ID_rank', 'GAMES_PLAYED_rank'], inplace = True)
full_stats_df

SEASON_ID  GAMES_PLAYED   WIN_PCT              tmp_id  \
0          22007             0  0.000000  207000011610612759   
1          22007             0  0.000000  207000021610612747   
2          22007             0  0.000000  207000021610612745   
3          22007             0  0.000000  207000011610612757   
4          22007             0  0.000000  207000031610612762   
...          ...           ...       ...                 ...   
38275      42021            18  0.666667  421004041610612744   
38276      42021            21  0.619048  421004051610612738   
38277      42021            19  0.684211  421004051610612744   
38278      42021            22  0.590909  421004061610612738   
38279      42021            20  0.700000  421004061610612744   

       SEASON_MA_PG_E_OFF_RATING  SEASON_MA_PG_OFF_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                 113.127778               114.733333   
38276                 109.238095               111.033333   
38277                 113.163158               114.800000   
38278                 108.650000               110.418182   
38279                 113.330000               114.995000   

       SEASON_MA_PG_E_DEF_RATING  SEASON_MA_PG_DEF_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                 112.505556               114.550000   
38276                 104.057143               105.409524   
38277                 111.852632               113.847368   
38278                 104.363636               105.686364   
38279                 111.185000               113.090000   

       SEASON_MA_PG_E_NET_RATING  SEASON_MA_PG_NET_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                   0.611111                 0.194444   
38276                   5.190476                 5.614286   
38277                   1.300000                 0.963158   
38278                   4.295455                 4.722727   
38279                   2.135000                 1.915000   

       SEASON_MA_PG_AST_PCT  SEASON_MA_PG_AST_TOV  SEASON_MA_PG_AST_RATIO  \
0                  0.000000              0.000000                0.000000   
1                  0.000000              0.000000                0.000000   
2                  0.000000              0.000000                0.000000   
3                  0.000000              0.000000                0.000000   
4                  0.000000              0.000000                0.000000   
...                     ...                   ...                     ...   
38275              0.265000              2.571111               20.522222   
38276              0.253714              2.960476               26.233333   
38277              0.261053              2.477895               19.984211   
38278              0.246955              2.848636               25.436364   
38279              0.261350              2.754000               20.235000   

       SEASON_MA_PG_OREB_PCT  SEASON_MA_PG_DREB_PCT  SEASON_MA_PG_REB_PCT  \
0                   0.000000         

In [ ]:
#merging dropped columns to calculate rank back to the gtp dataframe
gtp_df = gtp_df[['WL', 'TEAM_ID', 'GAME_ID', 'GAME_DATE_y', 'home_away', 'Final', 'WIN_TOTAL', 'LOSS_TOTAL', 'tmp_id', 'PG_PLAYER_ID', 'SG_PLAYER_ID', 'SF_PLAYER_ID', 'PF_PLAYER_ID', 'C_PLAYER_ID']]
gtp_df = pd.merge(gtp_df, full_stats_df, on = ['tmp_id'], how = 'outer')
gtp_df

WL     TEAM_ID   GAME_ID GAME_DATE_y home_away  Final  WIN_TOTAL  \
0       1  1610612759  20700001  2007-10-30         H    106        0.0   
1       0  1610612747  20700002  2007-10-30         H     93        0.0   
2       1  1610612745  20700002  2007-10-30         V     95        0.0   
3       0  1610612757  20700001  2007-10-30         V     97        0.0   
4       1  1610612762  20700003  2007-10-30         V    117        0.0   
...    ..         ...       ...         ...       ...    ...        ...   
38275   1  1610612744  42100404  2022-06-10         V    107       12.0   
38276   0  1610612738  42100405  2022-06-13         V     94       13.0   
38277   1  1610612744  42100405  2022-06-13         H    104       13.0   
38278   0  1610612738  42100406  2022-06-16         H     90       13.0   
38279   1  1610612744  42100406  2022-06-16         V    103       14.0   

       LOSS_TOTAL              tmp_id PG_PLAYER_ID SG_PLAYER_ID SF_PLAYER_ID  \
0             0.0  207000011610612759       2225.0        714.0       1477.0   
1             0.0  207000021610612747        965.0        977.0       2575.0   
2             0.0  207000021610612745       1747.0       1503.0       2203.0   
3             0.0  207000011610612757     101127.0     200750.0     101110.0   
4             0.0  207000031610612762     101114.0     200758.0       1905.0   
...           ...                 ...          ...          ...          ...   
38275         6.0  421004041610612744     201939.0     202691.0     203952.0   
38276         8.0  421004051610612738     203935.0    1627759.0    1628369.0   
38277         6.0  421004051610612744     201939.0     202691.0     203952.0   
38278         9.0  421004061610612738     203935.0    1627759.0    1628369.0   
38279         6.0  421004061610612744     201939.0     202691.0     203952.0   

      PF_PLAYER_ID C_PLAYER_ID  SEASON_ID  GAMES_PLAYED   WIN_PCT  \
0           1495.0    101177.0      22007             0  0.000000   
1         101142.0      2198.0      22007             0  0.000000   
2         101236.0      2397.0      22007             0  0.000000   
3         200746.0      2038.0      22007             0  0.000000   
4           2430.0      2246.0      22007             0  0.000000   
...            ...         ...        ...           ...       ...   
38275     203490.0    203110.0      42021            18  0.666667   
38276     201143.0   1629057.0      42021            21  0.619048   
38277     203490.0    203110.0      42021            19  0.684211   
38278     201143.0   1629057.0      42021            22  0.590909   
38279     203490.0    203110.0      42021            20  0.700000   

       SEASON_MA_PG_E_OFF_RATING  SEASON_MA_PG_OFF_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                 113.127778               114.733333   
38276                 109.238095               111.033333   
38277                 113.163158               114.800000   
38278                 108.650000               110.418182   
38279                 113.330000               114.995000   

       SEASON_MA_PG_E_DEF_RATING  SEASON_MA_PG_DEF_RATING  \
0                       0.000000                 0.000000   
1                       0.000000                 0.000000   
2                       0.000000                 0.000000   
3                       0.000000                 0.000000   
4                       0.000000                 0.000000   
...                          ...                      ...   
38275                 112.505556               114.550000   
38276                 104.057143               105.409524   
38277                 111.852632  

As specified above, we wouldn't have a model without generating target variables from bookmaker odds!

Due to some data quality issues from the bookermaker odds source, there's a bit more transformation that is needed to be done before creating these variables.

Aside from the usual `tmp_id` creation, this step is where we will split the dataframe by Home teams and Visiting teams, which is why the later stages in the previous data cleansing notebook were so important.

In [ ]:
odds_df = final_stats_spread[['GAME_ID', 'TEAM_ID', 'ML', 'spread_open', 'spread_close', 'spread_2H', 'total_open', 'total_close', 'total_2H']]
odds_df['tmp_id'] = odds_df['GAME_ID'].astype(str) + odds_df['TEAM_ID'].astype(str)
odds_df.drop(columns = ['GAME_ID', 'TEAM_ID'], inplace = True)
master_df = pd.merge(gtp_df, odds_df, on = ['tmp_id'], how = 'outer')

In [ ]:
h_df = master_df[master_df['home_away'] == 'H']
v_df = master_df[master_df['home_away'] == 'V']

In [ ]:
test_h = h_df.copy()

for col in test_h.columns:
    test_h.rename(columns = {col: f'{col}_home'}, inplace = True)
    
test_v = v_df.copy()

for col in test_v.columns:
    test_v.rename(columns = {col: f'{col}_away'}, inplace = True)
    
test_h.drop(columns = ['GAME_ID_x_home'], inplace = True)
test_h.rename(columns = {'GAME_ID_y_home': 'GAME_ID'}, inplace = True)
test_v.drop(columns = ['GAME_ID_x_away'], inplace = True)
test_v.rename(columns = {'GAME_ID_y_away': 'GAME_ID'}, inplace = True)

In [ ]:
master_vh = pd.merge(test_h, test_v, on = ['GAME_ID'], how = 'outer')

Above, we separated the dataframe by Home/Vistor, remained the columns accordingly, and then merged the two dataframe back together. The motivation for doing this is that moneyline (ML--*not machine learning*) and spreads are either negative or positive. More detail on this and their meaning in the report summary. The odds dataset we have properly specifies this for the moneyline, but not for the spreads.

This positive/negative relationship is mutually exclusive between the two opponents, and therefore it was much easier to properly designate this value when the values were in the same row.

When the moneyline is negative, that means that the team is favored, and therefore the spread is negative. If the moneyline is positive, this means that the team is the underdog and the spread is positive.

In [ ]:
master_vh['spread_open_home'] = np.where(master_vh['ML_home'] < 0, master_vh['spread_open_home'] * -1, master_vh['spread_open_home'])
master_vh['spread_open_away'] = np.where(master_vh['ML_away'] < 0, master_vh['spread_open_away'] * -1, master_vh['spread_open_away'])
master_vh[['ML_home', 'ML_away', 'spread_open_home', 'spread_open_away']]

ML_home  ML_away  spread_open_home  spread_open_away
0      -1400.0    900.0             -12.5              12.5
1        190.0   -230.0               2.5              -2.5
2       -120.0    100.0              -3.0               3.0
3       -125.0    105.0              -2.0               2.0
4        120.0   -140.0               3.0              -3.0
...        ...      ...               ...               ...
19135   -165.0    145.0              -2.0               2.0
19136   -155.0    135.0              -2.5               2.5
19137   -165.0    145.0              -2.5               2.5
19138   -165.0    145.0              -3.5               3.5
19139   -175.0    155.0              -2.5               2.5

[19140 rows x 4 columns]

Now that the betting lines are properly assigned, the next step is to generate the target variables.

The moneyline variable was the most straight forward--if a team wins, then the moneyline bet wins. The `WL` map that was created above can be leveraged for this.

The Over/Under variable is also fairly straight forward, as it represents the total number of points scored in the game across both teams. A summation of the final scores, compared with the betting line, will produce this binary class.

The spread variable is a bit more complex. If the spread is negative, that means that the favored team needs to win by more than the spread total for the bet to "hit". If the spread is positive, this means that the underdog team can still lose, but within the specified spread. I implemented some layered `np.where()` functions to implement this logic.

In [ ]:
master_vh['WL_outcome'] = np.where((master_vh['WL_home'] == 1), 1, 0)
master_vh = master_vh.drop(columns = ['WL_home', 'WL_away'])
master_vh['OU_hit'] = np.where((master_vh['Final_home'] + master_vh['Final_away']) > master_vh['total_open_away'], 1, 0)
master_vh['spread_hit'] = (
    np.where(
        (master_vh['ML_home'] < 0) & 
        (master_vh['Final_away'] - master_vh['Final_home'] < master_vh['spread_open_home']),
        1, 
        np.where(
            (master_vh['ML_home'] < 0) &
            (master_vh['Final_away'] - master_vh['Final_home'] > master_vh['spread_open_home']),
            0,
            np.where(
                (master_vh['ML_home'] > 0) &
                (master_vh['Final_home'] - master_vh['Final_away'] < master_vh['spread_open_away']),
                0,
                1
            )
        )
    )
)

Now that the target variables are created, we've successfully leveraged the bookmaker odds data for our initial model implementation.

A decision I've been going back-and-forth with is if the odds should be kept in the dataset as a feature. While it is publically available information that is known prior to the game being played, one could argue that it could be included. However, on the otherhand, I do fear of model biasing based on odds that were created from the bookmakers.

It will be excluded for now, but I may include it in the future to gauge model performance and if it does truly negatively bias the model.

In [ ]:
#dropping odds and game scores
master_vh.drop(columns = ['Final_home', 'Final_away', 'ML_away','spread_open_away','spread_close_away','spread_2H_away','total_open_away','total_close_away', 'total_2H_away', 'ML_home','spread_open_home','spread_close_home','spread_2H_home','total_open_home','total_close_home', 'total_2H_home'], inplace = True)

In [ ]:
#looking at remaining categorical variables
master_vh.select_dtypes(exclude = ['int', 'float'])

GAME_DATE_y_home home_away_home         tmp_id_home PG_PLAYER_ID_home  \
0           2007-10-30              H  207000011610612759            2225.0   
1           2007-10-30              H  207000021610612747             965.0   
2           2007-10-30              H  207000031610612744            1884.0   
3           2007-10-31              H  207000071610612751             467.0   
4           2007-10-31              H  207000081610612739          200789.0   
...                ...            ...                 ...               ...   
19135       2022-06-02              H  421004011610612744          201939.0   
19136       2022-06-08              H  421004031610612738          203935.0   
19137       2022-06-10              H  421004041610612738          203935.0   
19138       2022-06-13              H  421004051610612744          201939.0   
19139       2022-06-16              H  421004061610612738          203935.0   

      SG_PLAYER_ID_home SF_PLAYER_ID_home PF_PLAYER_ID_home C_PLAYER_ID_home  \
0                 714.0            1477.0            1495.0         101177.0   
1                 977.0            2575.0          101142.0           2198.0   
2              101145.0          101235.0            2554.0           2740.0   
3                1713.0            2210.0            2420.0           2215.0   
4                1716.0            2544.0            2400.0            980.0   
...                 ...               ...               ...              ...   
19135          202691.0          203952.0          203110.0        1626172.0   
19136         1627759.0         1628369.0          201143.0        1629057.0   
19137         1627759.0         1628369.0          201143.0        1629057.0   
19138          202691.0          203952.0          203490.0         203110.0   
19139         1627759.0         1628369.0          201143.0        1629057.0   

      TEAM_ID_x_home   GAME_ID TEAM_ID_y_home GAME_DATE_y_away home_away_away  \
0         1610612759  20700001     1610612759       2007-10-30              V   
1         1610612747  20700002     1610612747       2007-10-30              V   
2         1610612744  20700003     1610612744       2007-10-30              V   
3         1610612751  20700007     1610612751       2007-10-31              V   
4         1610612739  20700008     1610612739       2007-10-31              V   
...              ...       ...            ...              ...            ...   
19135     1610612744  42100401     1610612744       2022-06-02              V   
19136     1610612738  42100403     1610612738       2022-06-08              V   
19137     1610612738  42100404     1610612738       2022-06-10              V   
19138     1610612744  42100405     1610612744       2022-06-13              V   
19139     1610612738  42100406     1610612738       2022-06-16              V   

              tmp_id_away PG_PLAYER_ID_away SG_PLAYER_ID_away  \
0      207000011610612757          101127.0          200750.0   
1      207000021610612745            1747.0            1503.0   
2      207000031610612762          101114.0          200758.0   
3      207000071610612741            2550.0            2732.0   
4      207000081610612742            2734.0             224.0   
...                   ...               ...               ...   
19135  421004011610612738          203935.0         1627759.0   
19136  421004031610612744          201939.0          202691.0   
19137  421004041610612744          201939.0          202691.0   
19138  421004051610612738          203935.0         1627759.0   
19139  421004061610612744          201939.0          202691.0   

      SF_PLAYER_ID_away PF_PLAYER_ID_away C_PLAYER_ID_away TEAM_ID_x_away  \
0              101110.0          200746.0           2038.0     1610612757   
1                2203.0          101236.0           2397.0     1610612745   
2                1905.0            2430.0           2246.0     1610612762   
3                2736.0          2

In [ ]:
#changing PLAYER_IDs, GAME_IDs, TEAM_IDs back to numeric
master_vh['PG_PLAYER_ID_home'] = pd.to_numeric(master_vh['PG_PLAYER_ID_home'])
master_vh['SG_PLAYER_ID_home'] = pd.to_numeric(master_vh['SG_PLAYER_ID_home'])
master_vh['SF_PLAYER_ID_home'] = pd.to_numeric(master_vh['SF_PLAYER_ID_home'])
master_vh['PF_PLAYER_ID_home'] = pd.to_numeric(master_vh['PF_PLAYER_ID_home'])
master_vh['C_PLAYER_ID_home'] = pd.to_numeric(master_vh['C_PLAYER_ID_home'])
master_vh['PG_PLAYER_ID_away'] = pd.to_numeric(master_vh['PG_PLAYER_ID_away'])
master_vh['SG_PLAYER_ID_away'] = pd.to_numeric(master_vh['SG_PLAYER_ID_away'])
master_vh['SF_PLAYER_ID_away'] = pd.to_numeric(master_vh['SF_PLAYER_ID_away'])
master_vh['PF_PLAYER_ID_away'] = pd.to_numeric(master_vh['PF_PLAYER_ID_away'])
master_vh['C_PLAYER_ID_away'] = pd.to_numeric(master_vh['C_PLAYER_ID_away'])
master_vh['GAME_ID'] = pd.to_numeric(master_vh['GAME_ID'])
master_vh['TEAM_ID_y_home'] = pd.to_numeric(master_vh['TEAM_ID_y_home'])
master_vh['TEAM_ID_y_away'] = pd.to_numeric(master_vh['TEAM_ID_y_away'])

#renaming TEAM_ID_y_home
master_vh.rename(columns = {'TEAM_ID_y_home': 'TEAM_ID_home', 'TEAM_ID_y_away': 'TEAM_ID_away'}, inplace = True)

In [ ]:
#dropping dups
master_vh.drop(columns = ['GAME_DATE_y_home', 'home_away_home', 'home_away_away', 'TEAM_ID_x_home', 'TEAM_ID_x_away', 'tmp_id_away', 'tmp_id_home'], inplace = True)

For the game date, I decided to encode the day and month using the feature_engine CyclicalFeatures package and function. While there most likely won't be any incredibly strong signals, I thought the distance calculations between the days and the months was pretty sweet.

In [ ]:
master_vh['GAME_DATE_y_away'] = master_vh['GAME_DATE_y_away'].astype(str)
master_vh[['year', 'month', 'day']] = master_vh['GAME_DATE_y_away'].str.split('-', 2, expand = True)
master_vh = master_vh.astype({'year': 'int', 'month': 'int', 'day': 'int'})

In [ ]:
from feature_engine.creation import CyclicalFeatures

date_df = master_vh[['month', 'day']]

cyclical = CyclicalFeatures(variables = None, drop_original = True)

X = cyclical.fit_transform(date_df)

X.head()

month_sin  month_cos       day_sin  day_cos
0  -0.866025        0.5 -2.012985e-01  0.97953
1  -0.866025        0.5 -2.012985e-01  0.97953
2  -0.866025        0.5 -2.012985e-01  0.97953
3  -0.866025        0.5 -2.449294e-16  1.00000
4  -0.866025        0.5 -2.449294e-16  1.00000

In [ ]:
#adding the encoded days and months distances, dropping the date columns
master_vh[['month_sin', 'month_cos', 'day_sin', 'day_cos']] = X
master_vh.drop(columns = ['month', 'day', 'GAME_DATE_y_away'], inplace = True)

In [ ]:
master_vh.info(300)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 19140 entries, 0 to 19139
Data columns (total 2821 columns):
 #     Column                                 Dtype  
---    ------                                 -----  
 0     TEAM_ID_home                           int64  
 1     TEAM_ID_home                           int64  
 2     GAME_ID_home                           int64  
 3     WIN_TOTAL_home                         float64
 4     LOSS_TOTAL_home                        float64
 5     PG_PLAYER_ID_home                      float64
 6     SG_PLAYER_ID_home                      float64
 7     SF_PLAYER_ID_home                      float64
 8     PF_PLAYER_ID_home                      float64
 9     C_PLAYER_ID_home                       float64
 10    SEASON_ID_home                         int64  
 11    GAMES_PLAYED_home                      int64  
 12    WIN_PCT_home                           float64
 13    SEASON_MA_PG_E_OFF_RATING_home         float64
 14    SEASON_MA_PG_OFF_R

In [ ]:
#ensuring target variables are at the end of the df
master_vh = master_vh[[col for col in master_vh if col not in ['WL_outcome', 'OU_hit', 'spread_hit']] + ['WL_outcome', 'OU_hit', 'spread_hit']]

In [ ]:
master_vh.to_csv('final_nba_df.csv')